<a href="https://colab.research.google.com/github/pgimenes/fuzzy_carnival/blob/main/benchmarking/gnn_float32_benchmarking.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

Use MODELS and DATASETS arrays to define which models nd datasets to use in the training/inference steps

Model options: **gcn/gat/graphsage**

Dataset options: **Pubmed/Cora/Citeseer**



In [ ]:
# CONFIG
ACCELERATOR = "gpu"

MODELS = ["gcn", "gat", "graphsage"]
# MODELS = ["gcn"]
DATASETS = ["Pubmed", "Cora", "Citeseer"]
# DATASETS = ["Pubmed"]

Global Variables

In [ ]:
import os
import torch

# Define log directory for Pytorch Lightning
LOG_DIR = "gnn_"
if(torch.cuda.is_available):
  DEVICE_NAME = torch.cuda.get_device_name().replace(" ", "_")
  LOG_DIR = LOG_DIR + DEVICE_NAME
else:
  LOG_DIR = LOG_DIR + "cpu"

os.environ["LOG_DIR"] = LOG_DIR

# Check what GPU is available
!nvidia-smi

Tue Jan 17 09:07:40 2023       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 460.32.03    Driver Version: 460.32.03    CUDA Version: 11.2     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  Tesla T4            Off  | 00000000:00:04.0 Off |                    0 |
| N/A   55C    P8    11W /  70W |      3MiB / 15109MiB |      0%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------

In [ ]:
# Install required packages.
os.environ['TORCH'] = torch.__version__

!pip install -q torch-scatter -f https://data.pyg.org/whl/torch-${TORCH}.html --quiet
!pip install -q torch-sparse -f https://data.pyg.org/whl/torch-${TORCH}.html --quiet
!pip install -q git+https://github.com/pyg-team/pytorch_geometric.git --quiet
!pip install scipy==1.10.0 --quiet
!pip install pytorch-lightning --quiet

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 9.4/9.4 MB 63.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 4.5/4.5 MB 41.6 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 512.4/512.4 KB 13.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 280.2/280.2 KB 26.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 34.5/34.5 MB 29.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 800.3/800.3 KB 17.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 125.4/125.4 KB 16.5 MB/s eta 0:00:00


In [ ]:
# Import required packages
import numpy as np
import pandas as pd
import scipy

import torch.nn.functional as F
from torch.nn import Parameter

import torch_geometric
from torch_geometric.nn import GCNConv, GraphSAGE, SAGEConv, GATConv
from torch_geometric.loader import NeighborLoader, DataLoader
from torch_geometric.datasets import Planetoid
import torch_geometric.transforms as T
from torch_geometric.utils import to_networkx
from torch_geometric.utils.convert import to_networkx

import matplotlib.pyplot as plt
import networkx as nx

#set the device
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

import pytorch_lightning as pl
from pytorch_lightning.loggers import TensorBoardLogger

from datetime import datetime

Handle Dataset

In [ ]:
def define_dataset(name):
  if (name in ["Pubmed", "Cora", "Citeseer"]):
    dataset = Planetoid(root='.', name=name)
  else:
    dataset = None
  return dataset

In [ ]:
def print_dataset_info(dataset):
  data = dataset[0]
  print(f'Dataset: {dataset}')
  print('-------------------')
  print(f'Number of graphs: {len(dataset)}')
  print(f'Number of nodes: {data.x.shape[0]}')
  print(f'Number of features: {dataset.num_features}')
  print(f'Number of classes: {dataset.num_classes}')

  # Print information about the graph
  print(f'\nGraph:')
  print('------')
  print(f'Training nodes: {sum(data.train_mask).item()}')
  print(f'Evaluation nodes: {sum(data.val_mask).item()}')
  print(f'Test nodes: {sum(data.test_mask).item()}')
  print(f'Edges are directed: {data.is_directed()}')
  print(f'Graph has isolated nodes: {data.has_isolated_nodes()}')
  print(f'Graph has loops: {data.has_self_loops()}')

In [ ]:
#Visualize the graph using networkx
# plt.figure(figsize=(10, 10))
# pubmed = torch_geometric.data.Data(x=data.x[:500], edge_index=data.edge_index[:500])
# g = torch_geometric.utils.to_networkx(pubmed, to_undirected=True)
# pubmedGraph = to_networkx(pubmed)
# node_labels = data.y[list(pubmedGraph.nodes)].numpy()
# nx.draw(g, cmap=plt.get_cmap('Set1'),node_color = node_labels,node_size=75,linewidths=6)

Declare models

*   GCN
*   GAT
*   GraphSAGE

In [ ]:
'''
Graph Convolutional Network
GCN takes graphs as an input and applies convolution operations over the graph
'''
class GCN(pl.LightningModule):
  def __init__(self):
    super().__init__()
    self.conv1 = GCNConv(dataset.num_node_features, 16)
    self.conv2 = GCNConv(16, dataset.num_classes)
    
  def forward(self, x, edge_index):
    x = self.conv1(x, edge_index)
    x = F.relu(x)
    x = F.dropout(x, training=self.training)
    x = self.conv2(x, edge_index)
    return F.log_softmax(x, dim=1)

In [ ]:
'''
Graph Attention Network
'''
class GAT(pl.LightningModule):
  def __init__(self):
    super().__init__()

    self.hid = 8
    self.in_head = 8
    self.out_head = 1

    self.conv1 = GATConv(dataset.num_node_features, self.hid, self.in_head, dropout=0.6)
    
    self.conv2 = GATConv(self.hid*self.in_head, dataset.num_classes, concat=False,
                         heads=self.out_head, dropout=0.6)
    
  def forward(self, x, edge_index):
    x = F.dropout(x, p=0.6, training=self.training)
    x = self.conv1(x, edge_index)
    x = F.elu(x)
    x = F.dropout(x, p=0.5, training=self.training)
    x = self.conv2(x, edge_index)
    return F.log_softmax(x, dim=1)

In [ ]:
'''
GraphSAGE
'''
class GraphSAGE(pl.LightningModule):
  def __init__(self):
    super().__init__()

    self.dim_in = dataset.num_features
    self.dim_h = 64
    self.dim_out = dataset.num_classes

    self.sage1 = SAGEConv(self.dim_in, self.dim_h*2)
    self.sage2 = SAGEConv(self.dim_h*2, self.dim_h)
    self.sage3 = SAGEConv(self.dim_h, self.dim_out)
    
  def forward(self, x, edge_index):
    x = self.sage1(x, edge_index)
    x = torch.relu(x)
    x = F.dropout(x, p=0.5, training=self.training)
    x = self.sage2(x, edge_index)
    x = torch.relu(x)
    x = F.dropout(x, p=0.2, training=self.training)
    x = self.sage3(x, edge_index)
    return F.log_softmax(x, dim=1)

PyTorch Lightning Wrapper

In [ ]:
class GNN(pl.LightningModule):
  def __init__(self, model):
    super().__init__()

    # Define model based on constructor argument
    if (model == "gcn"):
      self.model = GCN()
    elif (model == "gat"):
      self.model = GAT()
    elif (model == "graphsage"):
      self.model = GraphSAGE()
    else:
      self.model = None

    self.starter, self.ender = torch.cuda.Event(enable_timing=True), torch.cuda.Event(enable_timing=True)
    self.loss_criterion = torch.nn.CrossEntropyLoss(reduction="sum")

  def forward(self, x, edge_index):
    return self.model(x, edge_index)

  def training_step(self, batch, batch_index):
    x, edge_index = batch.x, batch.edge_index
    y = batch.y

    out = self.forward(x, edge_index)

    # need to mask out trained nodes?
    loss = self.loss_criterion(out[batch.train_mask], y[batch.train_mask])

    # prediction is maximum likelihood from log softmax probabilities
    pred = out[batch.train_mask].argmax(dim=1) # dim=1 : per row
    acc = self.accuracy(pred, y[batch.train_mask])

    self.log("loss/train", loss)
    self.log("accuracy/train", acc)

    return loss

  def validation_step(self, batch, batch_index):
    x, edge_index = batch.x, batch.edge_index
    y = batch.y

    # Compute forward pass for entire batch (train + val)
    out = self.forward(x, edge_index)

    loss = self.loss_criterion(out[batch.val_mask], y[batch.val_mask])
    pred = out[batch.val_mask].argmax(dim=1)
    return out[batch.val_mask], pred, y[batch.val_mask]

  def validation_epoch_end(self, validation_step_outputs):
    val_loss = 0
    num_correct = 0
    num_total = 0

    for out, pred, labels in validation_step_outputs:
      val_loss += self.loss_criterion(out, labels)
      num_correct += (pred == labels).sum()
      num_total += pred.shape[0]
      
      val_accuracy = num_correct / num_total
      val_loss = val_loss/num_total

    self.log("accuracy/val", val_accuracy)
    self.log("loss/val", val_loss)

  def predict_step(self, batch, batch_index):
    x, edge_index = batch.x, batch.edge_index
    torch.cuda.empty_cache()
    self.starter.record()
    _ = self.model(x, edge_index)
    self.ender.record()
    torch.cuda.synchronize()
    inference_time = self.starter.elapsed_time(self.ender)
    return inference_time

  def configure_optimizers(self):
    return torch.optim.Adam(self.parameters(), lr=0.005, weight_decay=5e-4)

  def accuracy(self, pred_y, y):
    """Calculate accuracy."""
    return ((pred_y == y).sum() / len(y)).item()

In [ ]:
def define_logger (dataset, model):
  logger_name = dataset + "_" + model
  return TensorBoardLogger(LOG_DIR, name=logger_name)

def train_model(model, dataloader):
  trainer.fit(model, dataloader, dataloader)

# Create batches with neighbor sampling
#A NeighborLoader is a data loader that performs neighbor sampling for GNN's
#Allows for mini-batch training of GNNs on large-scale graphs where full-batch training is not feasible.
#num_neighbors denotes how many neighbors are sampled for each node in each iteration.
#https://pytorch-geometric.readthedocs.io/en/latest/modules/loader.html#torch_geometric.loader.NeighborLoader

# train_loader = NeighborLoader(
#     data,
#     num_neighbors=[5, 10],
#     batch_size=16,
#     input_nodes=data.train_mask,
# )

Training Loop

In [ ]:
epochs = 10

inference_times = pd.DataFrame(dict.fromkeys(DATASETS), index=MODELS)

for dts in DATASETS:
  dataset = define_dataset(dts)
  print_dataset_info(dataset)
  
  for model in MODELS:
    gnn = GNN(model)

    tloader = DataLoader(dataset, batch_size=1)

    logger = define_logger(dts, model)

    trainer = pl.Trainer(max_epochs=epochs, \
                    val_check_interval=1, \
                    log_every_n_steps=1, \
                    logger=logger, \
                    accelerator=ACCELERATOR)
    
    train_model(gnn, tloader)

    times = []
    for i in range(0, 50):
      inference_time = trainer.predict(model=gnn, dataloaders=tloader)
      times = times + [inference_time]
    
    inference_times.at[model, dts] = inference_time[0]

# plt.plot(list(range(0, 50)), times)
# plt.show()

# Export inference times
timestamp = datetime.now().strftime("%d_%m_%Y_%H_%M_%S")
fname = "inference_times_" + DEVICE_NAME + "_" + timestamp + ".csv"
inference_times.to_csv(fname)

# Visualize metrics
# %reload_ext tensorboard
# %tensorboard --logdir=$LOG_DIR/

Processing...
Done!


Dataset: Pubmed()
-------------------
Number of graphs: 1
Number of nodes: 19717
Number of features: 500
Number of classes: 3

Graph:
------
Training nodes: 60
Evaluation nodes: 500


/usr/local/lib/python3.8/dist-packages/torch_geometric/deprecation.py:18: UserWarning: 'data.DataLoader' is deprecated, use 'loader.DataLoader' instead
  warnings.warn(out)
INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True


Test nodes: 1000
Edges are directed: False
Graph has isolated nodes: False
Graph has loops: False


INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:IPU available: False, using: 0 IPUs
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.utilities.rank_zero:`Trainer(val_check_interval=1)` was configured so validation will run after every batch.
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:pytorch_lightning.callbacks.model_summary:
  | Name           | Type             | Params
----------------------------------------------------
0 | model          | GCN              | 8.1 K 
1 | loss_criterion | CrossEntropyLoss | 0     
----------------------------------------------------
8.1 K     Trainable params
0         Non-trainable params
8.1 K     Total params
0.032     Total estimated model params size (MB)


...

Predicting: 1it [00:00, ?it/s]

INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Predicting: 1it [00:00, ?it/s]

INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Predicting: 1it [00:00, ?it/s]